In [1]:
import pandas as pd
import pymssql
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np

from matplotlib_venn import venn2, venn2_circles, venn2_unweighted
from matplotlib_venn import venn3, venn3_circles, venn3_unweighted
from matplotlib import pyplot as plt
import scipy.stats as stats
import plotly.graph_objects as go
import plotly.express as px


In [2]:
from config import database
from config import Mouse
from config import Virus
from config import Protein
from config import Biotin
from config import Fraction
from config import Protein_Id
from config import Gene
from config import Protein_Description
from config import Peptide
from config import username
from config import password
from config import server

In [3]:
try:
    conn = pymssql.connect(server,username, password,database)

    cursor = conn.cursor()
    query = f"""
    SELECT 
        M.Sample_Name,
        P.Protein_Name,
        V.Virus_Label,
        B.Biotin_Label,
        F.Fraction_Label,
        MP.Hits
        FROM Mouse_Protein AS MP 
    INNER JOIN {Mouse} AS M on MP.Mouse_ID = M.Mouse_ID
    INNER JOIN {Protein} AS P on MP.Protein_ID = P.Protein_ID
    INNER JOIN {Virus} AS V on M.Virus_ID = V.Virus_ID
    INNER JOIN {Biotin} AS B on M.Biotin_ID = B.Biotin_ID
    INNER JOIN {Fraction} AS F on M.Fraction_ID = F.Fraction_ID
    INNER JOIN {Protein_Id} AS PI on P.Protein_Id_ID = PI.Protein_Id_ID
    INNER JOIN {Gene} AS G on P.Gene_ID = G.Gene_ID
    INNER JOIN {Protein_Description} AS PD on P.Description_ID = PD.Description_ID
    INNER JOIN {Peptide} AS PE on P.Peptide_ID = PE.Peptide_ID
    WHERE M.Sample_Name != 'Q331K_M1' AND M.Sample_Name != 'Q331K_M2' AND M.Sample_Name != 'WT_M3' AND M.Sample_Name != 'WT_M4'
    ORDER BY MP.Hits DESC
    """
    main_df = pd.read_sql(query, conn)
except Exception as e:
    print(e)
main_df.head()

Sample_Name                                       Protein_Name  \
0  3062-MRU-LP1_11                                          NFH_MOUSE   
1  3062-MRU-LP1_11                                          NFL_MOUSE   
2  3062-MRU-LP1_11  H2A1B_MOUSE;H2A1C_MOUSE;H2A1D_MOUSE;H2A1E_MOUS...   
3  3062-MRU-LP1_11                                        TBA1A_MOUSE   
4  3062-MRU-LP1_11             PLEC-6_MOUSE;PLEC-7_MOUSE;PLEC-8_MOUSE   

     Virus_Label Biotin_Label Fraction_Label          Hits  
0  TDP43-TurboID           72            LP1  5.225510e+09  
1  TDP43-TurboID           72            LP1  4.174620e+09  
2  TDP43-TurboID           72            LP1  3.127040e+09  
3  TDP43-TurboID           72            LP1  3.018330e+09  
4  TDP43-TurboID           72            LP1  2.856640e+09

In [4]:
print("Virus types:", list(main_df["Virus_Label"].unique()))
print("Biotin types:", list(main_df["Biotin_Label"].unique()))
print("Fraction types:", list(main_df["Fraction_Label"].unique()))
print("Total rows of data:", len(main_df), "\nWith 24 data frame combos")

Virus types: ['TDP43-TurboID', 'TurboID']
Biotin types: ['72', '1.5', 'saline']
Fraction types: ['LP1', 'LS1', 'whole brain', 'Nuclear']
Total rows of data: 115317 
With 24 data frame combos


In [5]:
# Virus type _ Biotin type _ Fraction Type  =  labeling scheme for dfs

# TurboID virus & 72 Biotin combonations
TurboID_72_LP1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LP1"]
TurboID_72_wholebrain = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "whole brain"]
TurboID_72_LS1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LS1"]
TurboID_72_Nuclear = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "Nuclear"]

# TurboID virus & 1.5 Biotin combonations
TurboID_15_LP1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "LP1"]
TurboID_15_wholebrain = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "whole brain"]
TurboID_15_LS1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "LS1"]
TurboID_15_Nuclear = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "Nuclear"]

# TurboID virus & saline Biotin combonations
TurboID_saline_LP1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LP1"]
TurboID_saline_wholebrain = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "whole brain"]
TurboID_saline_LS1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LS1"]
TurboID_saline_Nuclear = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "Nuclear"]

# TDP43-TurboID virus & 72 Biotin combonations
TDP43TurboID_72_LP1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LP1"]
TDP43TurboID_72_wholebrain = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "whole brain"]
TDP43TurboID_72_LS1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LS1"]
TDP43TurboID_72_Nuclear = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "Nuclear"]

# TDP43-TurboID virus & 1.5 Biotin combonations
TDP43TurboID_15_LP1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "LP1"]
TDP43TurboID_15_wholebrain = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "whole brain"]
TDP43TurboID_15_LS1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "LS1"]
TDP43TurboID_15_Nuclear = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "1.5"][main_df["Fraction_Label"] == "Nuclear"]

# TDP43-TurboID virus & saline Biotin combonations
TDP43TurboID_saline_LP1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LP1"]
TDP43TurboID_saline_wholebrain = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "whole brain"]
TDP43TurboID_saline_LS1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LS1"]
TDP43TurboID_saline_Nuclear = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "Nuclear"]

# Total amount of row captured check, should get a total of zero
print("Should be zero:", len(main_df) - (len(TurboID_72_LP1) + len(TurboID_72_wholebrain) + len(TurboID_72_LS1) + len(TurboID_72_Nuclear)
                    + len(TurboID_15_LP1) + len(TurboID_15_wholebrain) + len(TurboID_15_LS1) + len(TurboID_15_Nuclear)
                    + len(TurboID_saline_LP1) + len(TurboID_saline_wholebrain) + len(TurboID_saline_LS1) + len(TurboID_saline_Nuclear)
                    
                    + len(TDP43TurboID_72_LP1) + len(TDP43TurboID_72_wholebrain) + len(TDP43TurboID_72_LS1) + len(TDP43TurboID_72_Nuclear)
                    + len(TDP43TurboID_15_LP1) + len(TDP43TurboID_15_wholebrain) + len(TDP43TurboID_15_LS1) + len(TDP43TurboID_15_Nuclear)
                    + len(TDP43TurboID_saline_LP1) + len(TDP43TurboID_saline_wholebrain) + len(TDP43TurboID_saline_LS1) + len(TDP43TurboID_saline_Nuclear)))

C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TurboID_72_LP1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LP1"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:5: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TurboID_72_wholebrain = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "whole brain"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:6: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TurboID_72_LS1 = main_df[main_df["Virus_Label"] == "TurboID"][main_df["Biotin_Label"] == "72"][main_df["Fraction_Label"] == "LS1"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:7: UserWarning: Boolean Series key will be reindexed to match DataFra

Should be zero: 0


C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:34: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TDP43TurboID_saline_LP1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LP1"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:35: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TDP43TurboID_saline_wholebrain = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "whole brain"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:36: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  TDP43TurboID_saline_LS1 = main_df[main_df["Virus_Label"] == "TDP43-TurboID"][main_df["Biotin_Label"] == "saline"][main_df["Fraction_Label"] == "LS1"]
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1740437975.py:37: UserW

In [6]:
TurboID_72_LP1 = TurboID_72_LP1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TurboID_72_LP1"})
TurboID_72_wholebrain = TurboID_72_wholebrain[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TurboID_72_wholebrain"})
TurboID_72_LS1 = TurboID_72_LS1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TurboID_72_LS1"})
TurboID_15_wholebrain = TurboID_15_wholebrain[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TurboID_15_wholebrain"})

# Told this experiment went poorly
# TDP43TurboID_72_LP1 = TDP43TurboID_72_LP1.rename(columns = {"Hits": "TDP43TurboID_72_LP1"})

TDP43TurboID_72_wholebrain = TDP43TurboID_72_wholebrain[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_72_wholebrain"})
TDP43TurboID_72_LS1 = TDP43TurboID_72_LS1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_72_LS1"})
TDP43TurboID_15_LP1 = TDP43TurboID_15_LP1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_15_LP1"})
TDP43TurboID_15_wholebrain = TDP43TurboID_15_wholebrain[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_15_wholebrain"})
TDP43TurboID_15_LS1 = TDP43TurboID_15_LS1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_15_LS1"})
TDP43TurboID_15_Nuclear = TDP43TurboID_15_Nuclear[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_15_Nuclear"})
TDP43TurboID_saline_LP1 = TDP43TurboID_saline_LP1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_saline_LP1"})
TDP43TurboID_saline_LS1 = TDP43TurboID_saline_LS1[["Protein_Name", "Hits"]].rename(columns = {"Hits": "TDP43TurboID_saline_LS1"})

print("Should be zero:", len(main_df) - (len(TurboID_72_LP1) + len(TurboID_72_wholebrain) + len(TurboID_72_LS1) 
                    + len(TurboID_15_wholebrain) + len(TDP43TurboID_72_wholebrain) + len(TDP43TurboID_72_LS1) 
                    + len(TDP43TurboID_15_LP1) + len(TDP43TurboID_15_wholebrain) + len(TDP43TurboID_15_LS1) 
                     + len(TDP43TurboID_15_Nuclear) + len(TDP43TurboID_saline_LP1) + len(TDP43TurboID_saline_LS1))    - len(TDP43TurboID_72_LP1))


Should be zero: 0


In [7]:
merge_df = TurboID_72_LP1.merge(TurboID_72_wholebrain, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TurboID_72_LS1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TurboID_15_wholebrain, how = "inner", on = "Protein_Name")
# merge_df = merge_df.merge(TDP43TurboID_72_LP1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_72_wholebrain, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_72_LS1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_15_LP1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_15_wholebrain, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_15_LS1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_15_Nuclear, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_saline_LP1, how = "inner", on = "Protein_Name")
merge_df = merge_df.merge(TDP43TurboID_saline_LS1, how = "inner", on = "Protein_Name")
merge_df

Protein_Name  TurboID_72_LP1  TurboID_72_wholebrain  \
0                       NFH_MOUSE     377871000.0             31793600.0   
1                       NFH_MOUSE     377871000.0             31793600.0   
2                       NFH_MOUSE     377871000.0             31793600.0   
3                       NFH_MOUSE     377871000.0             31793600.0   
4                       NFH_MOUSE     377871000.0             31793600.0   
...                           ...             ...                    ...   
185959                 NOE2_MOUSE             0.0                    0.0   
185960  GARL3-2_MOUSE;GARL3_MOUSE             0.0                    0.0   
185961  GARL3-2_MOUSE;GARL3_MOUSE             0.0                    0.0   
185962  GARL3-2_MOUSE;GARL3_MOUSE             0.0                    0.0   
185963  GARL3-2_MOUSE;GARL3_MOUSE             0.0                    0.0   

        TurboID_72_LS1  TurboID_15_wholebrain  TDP43TurboID_72_wholebrain  \
0            2131870.0              4852130.0                  15509000.0   
1            2131870.0              4852130.0                  11760800.0   
2            2131870.0              4852130.0                   2382530.0   
3            2131870.0              4852130.0                   2382530.0   
4            2131870.0              4852130.0                   2382530.0   
...                ...                    ...                         ...   
185959             0.0                    0.0                         0.0   
185960             0.0                    0.0                     97530.7   
185961             0.0                    0.0                         0.0   
185962             0.0                    0.0                     97530.7   
185963             0.0                    0.0                         0.0   

        TDP43TurboID_72_LS1  TDP43TurboID_15_LP1  TDP43TurboID_15_wholebrain  \
0                16590700.0           36090300.0                   3218000.0   
1                16590700.0           36090300.0                   3218000.0   
2                16590700.0           36090300.0                   3218000.0   
3                16590700.0           36090300.0                   3218000.0   
4                16590700.0           36090300.0                   3218000.0   
...                     ...                  ...                         ...   
185959                  0.0                  0.0                         0.0   
185960              93561.1             108678.0                         0.0   
185961              93561.1             108678.0                         0.0   
185962              93561.1             108678.0                         0.0   
185963              93561.1             108678.0                         0.0   

        TDP43TurboID_15_LS1  TDP43TurboID_15_Nuclear  TDP43TurboID_saline_LP1  \
0                17141700.0                1197810.0               32875900.0   
1                17141700.0                1197810.0               32875900.0   
2                17141700.0                1197810.0               32875900.0   
3                17141700.0                1197810.0               32875900.0   
4                17141700.0                1197810.0               32875900.0   
...                     ...                      ...                      ...   
185959                  0.0                      0.0                      0.0   
185960             490093.0                      0.0                 268032.0   
185961             490093.0                      0.0                 268032.0   
185962             490093.0                      0.0                 268032.0   
185963             490093.0                      0.0                 268032.0   

        TDP43TurboID_saline_LS1  
0                     4808820.0  
1                     4808820.0  
2                     4808820.0  
3                     4808820.0  
4                     4808820.0  
...                         ...  
185959     

In [8]:
merge_df.describe()

TurboID_72_LP1  TurboID_72_wholebrain  TurboID_72_LS1  \
count    1.859640e+05           1.859640e+05    1.859640e+05   
mean     1.709280e+06           4.465350e+05    3.418340e+05   
std      1.460137e+07           5.688293e+06    4.007230e+06   
min      0.000000e+00           0.000000e+00    0.000000e+00   
25%      0.000000e+00           0.000000e+00    0.000000e+00   
50%      1.671230e+05           2.094090e+04    0.000000e+00   
75%      5.437060e+05           7.370410e+04    0.000000e+00   
max      3.778710e+08           2.747850e+08    1.527480e+08   

       TurboID_15_wholebrain  TDP43TurboID_72_wholebrain  TDP43TurboID_72_LS1  \
count           1.859640e+05                1.859640e+05         1.859640e+05   
mean            4.406750e+05                7.295708e+05         9.320734e+05   
std             3.289367e+06                5.129691e+06         4.229897e+06   
min             0.000000e+00                0.000000e+00         0.000000e+00   
25%             0.000000e+00                3.325740e+04         0.000000e+00   
50%             0.000000e+00                8.416160e+04         1.785040e+05   
75%             4.607480e+04                2.569920e+05         5.040500e+05   
max             9.837660e+07                2.734620e+08         1.006870e+08   

       TDP43TurboID_15_LP1  TDP43TurboID_15_wholebrain  TDP43TurboID_15_LS1  \
count         1.859640e+05                1.859640e+05         1.859640e+05   
mean          2.469001e+06                5.272838e+05         7.236318e+06   
std           8.952643e+06                3.787972e+06         3.244063e+07   
min           0.000000e+00                0.000000e+00         0.000000e+00   
25%           2.187000e+05                0.000000e+00         4.131480e+05   
50%           6.043250e+05                0.000000e+00         1.368370e+06   
75%           1.601930e+06                8.001240e+04         4.662490e+06   
max           1.617830e+08                9.074820e+07         8.995690e+08   

       TDP43TurboID_15_Nuclear  TDP43TurboID_saline_LP1  \
count             1.859640e+05             1.859640e+05   
mean              6.294389e+05             3.464203e+06   
std               6.654092e+06             1.262072e+07   
min               0.000000e+00             0.000000e+00   
25%               0.000000e+00             3.155070e+05   
50%               0.000000e+00             8.814470e+05   
75%               0.000000e+00             2.266070e+06   
max               1.712900e+08             2.482360e+08   

       TDP43TurboID_saline_LS1  
count             1.859640e+05  
mean              1.814174e+05  
std               1.531939e+06  
min               0.000000e+00  
25%               0.000000e+00  
50%               0.000000e+00  
75%               0.000000e+00  
max               5.749860e+07

In [9]:
merge_df_plotly = merge_df.copy()
merge_df_bioinfokit = merge_df.copy()

---
# Bioinfokit Volcano Plot

In [10]:
from bioinfokit import analys, visuz
# load dataset as pandas dataframe
df = analys.get_data('volcano').data
# visuz.GeneExpression.volcano(df=df, lfc='log2FC', pv='p-value')

---
# Ploty Volcano Plot

In [11]:
# z score
# stats.zscore(list)

# p value
# p = [stats.norm.sf(abs(x)) for x in list]

merge_df_plotly.replace([0, np.NaN], 1, inplace=True)


merge_df_plotly["TurboID_72_LP1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_72_LP1"].to_list())])
merge_df_plotly["TurboID_72_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_72_wholebrain"].to_list())])
merge_df_plotly["TurboID_72_LS1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_72_LS1"].to_list())])
merge_df_plotly["TurboID_15_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_15_wholebrain"].to_list())])
merge_df_plotly["TDP43TurboID_72_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_72_wholebrain"].to_list())])
merge_df_plotly["TDP43TurboID_72_LS1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_72_LS1"].to_list())])
merge_df_plotly["TDP43TurboID_15_LP1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_15_LP1"].to_list())])
merge_df_plotly["TDP43TurboID_15_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_15_wholebrain"].to_list())])
merge_df_plotly["TDP43TurboID_15_LS1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_15_LS1"].to_list())])
merge_df_plotly["TDP43TurboID_15_Nuclear_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_15_Nuclear"].to_list())])
merge_df_plotly["TDP43TurboID_saline_LP1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_saline_LP1"].to_list())])
merge_df_plotly["TDP43TurboID_saline_LS1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_saline_LS1"].to_list())])


# log2(FC)
merge_df_plotly["TurboID_72_LP1_log2FC"] = np.log2(merge_df_plotly["TurboID_72_LP1"].to_list())
merge_df_plotly["TurboID_72_wholebrain_log2FC"] = np.log2(merge_df_plotly["TurboID_72_wholebrain"].to_list())
merge_df_plotly["TurboID_72_LS1_log2FC"] = np.log2(merge_df_plotly["TurboID_72_LS1"].to_list())
merge_df_plotly["TurboID_15_wholebrain_log2FC"] = np.log2(merge_df_plotly["TurboID_15_wholebrain"].to_list())
merge_df_plotly["TDP43TurboID_72_wholebrain_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_72_wholebrain"].to_list())
merge_df_plotly["TDP43TurboID_72_LS1_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_72_LS1"].to_list())
merge_df_plotly["TDP43TurboID_15_LP1_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_15_LP1"].to_list())
merge_df_plotly["TDP43TurboID_15_wholebrain_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_15_wholebrain"].to_list())
merge_df_plotly["TDP43TurboID_15_LS1_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_15_LS1"].to_list())
merge_df_plotly["TDP43TurboID_15_Nuclear_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_15_Nuclear"].to_list())
merge_df_plotly["TDP43TurboID_saline_LP1_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_saline_LP1"].to_list())
merge_df_plotly["TDP43TurboID_saline_LS1_log2FC"] = np.log2(merge_df_plotly["TDP43TurboID_saline_LS1"].to_list())

def reset_columns(df):
    columns_list = df.columns.tolist()
    columns_list.remove("Protein_Name")
    columns_list.sort()
    columns_list = ["Protein_Name"] + columns_list
    return df[columns_list]

merge_df_plotly = reset_columns(merge_df_plotly)
merge_df_plotly.replace([-np.inf, np.NaN], 0, inplace=True)


merge_df_plotly = merge_df_plotly.groupby("Protein_Name", as_index=False).mean()
merge_df_plotly

C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1105606364.py:11: RuntimeWarning: divide by zero encountered in log10
  merge_df_plotly["TurboID_72_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_72_wholebrain"].to_list())])
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1105606364.py:12: RuntimeWarning: divide by zero encountered in log10
  merge_df_plotly["TurboID_72_LS1_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TurboID_72_LS1"].to_list())])
C:\Users\Adam Brewer\AppData\Local\Temp\ipykernel_21112\1105606364.py:14: RuntimeWarning: divide by zero encountered in log10
  merge_df_plotly["TDP43TurboID_72_wholebrain_neg_log_pval"] = (-1) * np.log10([stats.norm.sf(abs(x)) for x in stats.zscore(merge_df_plotly["TDP43TurboID_72_wholebrain"].to_list())])


Protein_Name  TDP43TurboID_15_LP1  \
0     1433B-2_MOUSE;1433B_MOUSE            1317030.0   
1                   1433E_MOUSE            3213180.0   
2                   1433F_MOUSE            3094950.0   
3                   1433G_MOUSE            7584630.0   
4                   1433S_MOUSE            1755150.0   
...                         ...                  ...   
5878                 ZW10_MOUSE             300842.0   
5879                ZWINT_MOUSE             323275.0   
5880                ZY11B_MOUSE             144457.0   
5881                  ZYX_MOUSE                  1.0   
5882  ZZEF1-2_MOUSE;ZZEF1_MOUSE             112824.0   

      TDP43TurboID_15_LP1_log2FC  TDP43TurboID_15_LP1_neg_log_pval  \
0                      20.328857                          0.347940   
1                      21.615570                          0.330798   
2                      21.561485                          0.325939   
3                      22.854647                          0.546895   
4                      20.743163                          0.329547   
...                          ...                               ...   
5878                   18.198646                          0.393275   
5879                   18.302402                          0.392233   
5880                   17.140281                          0.400590   
5881                    0.000000                          0.407427   
5882                   16.783714                          0.402080   

      TDP43TurboID_15_LS1  TDP43TurboID_15_LS1_log2FC  \
0               4833230.0                   22.204556   
1               9148930.0                   23.125172   
2              11647800.0                   23.473554   
3              29505600.0                   24.814485   
4              16232900.0                   23.952417   
...                   ...                         ...   
5878                  1.0                    0.000000   
5879             633080.0                   19.272028   
5880             568167.0                   19.115956   
5881             953699.0                   19.863174   
5882             425839.0                   18.699949   

      TDP43TurboID_15_LS1_neg_log_pval  TDP43TurboID_15_Nuclear  \
0                             0.327464                      1.0   
1                             0.321943                      1.0   
2                             0.350747                      1.0   
3                             0.608694                      1.0   
4                             0.408084                 359152.0   
...                                ...                      ...   
5878                          0.385374                      1.0   
5879                          0.377420                      1.0   
5880                          0.378231                      1.0   
5881                          0.373435                      1.0   
5882                          0.380012                      1.0   

      TDP43TurboID_15_Nuclear_log2FC  TDP43TurboID_15_Nuclear_neg_log_pval  \
0                           0.000000                              0.335059   
1                           0.000000                              0.335059   
2                           0.000000                              0.335059   
3                           0.000000                              0.335059   
4                          18.454235                              0.315335   
...                              ...                                   ...   
5878                        0.000000                              0.335059   
5879                        0.000000                              0.335059   
5880                        0.000000                              0.335059   
5881                        0.000000                              0.335059   
5882                        0.000000                              0.335059   

      ...  TurboID_15_wholebrain_neg_log_pval  TurboID_72_LP1  \
0     ...    

In [12]:
columns = merge_df_plotly.columns.to_list()
count = 0
for col in range(len(columns)):
    if(columns[col] == "Protein_Name"):
        continue
    else:
        print(columns[col],"    |   ", end='')
        count += 1
        if(count % 3 == 0):
            print()

TDP43TurboID_15_LP1     |   TDP43TurboID_15_LP1_log2FC     |   TDP43TurboID_15_LP1_neg_log_pval     |   
TDP43TurboID_15_LS1     |   TDP43TurboID_15_LS1_log2FC     |   TDP43TurboID_15_LS1_neg_log_pval     |   
TDP43TurboID_15_Nuclear     |   TDP43TurboID_15_Nuclear_log2FC     |   TDP43TurboID_15_Nuclear_neg_log_pval     |   
TDP43TurboID_15_wholebrain     |   TDP43TurboID_15_wholebrain_log2FC     |   TDP43TurboID_15_wholebrain_neg_log_pval     |   
TDP43TurboID_72_LS1     |   TDP43TurboID_72_LS1_log2FC     |   TDP43TurboID_72_LS1_neg_log_pval     |   
TDP43TurboID_72_wholebrain     |   TDP43TurboID_72_wholebrain_log2FC     |   TDP43TurboID_72_wholebrain_neg_log_pval     |   
TDP43TurboID_saline_LP1     |   TDP43TurboID_saline_LP1_log2FC     |   TDP43TurboID_saline_LP1_neg_log_pval     |   
TDP43TurboID_saline_LS1     |   TDP43TurboID_saline_LS1_log2FC     |   TDP43TurboID_saline_LS1_neg_log_pval     |   
TurboID_15_wholebrain     |   TurboID_15_wholebrain_log2FC     |   TurboID_15_whol

In [13]:
opacity = 0.6; size = 10

trace1 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_15_LP1_log2FC'],
 y=merge_df_plotly['TDP43TurboID_15_LP1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_15_LP1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace2 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_15_LS1_log2FC'],
 y=merge_df_plotly['TDP43TurboID_15_LS1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_15_LS1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace3 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_15_Nuclear_log2FC'],
 y=merge_df_plotly['TDP43TurboID_15_LS1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_15_LS1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace4 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_15_wholebrain_log2FC'],
 y=merge_df_plotly['TDP43TurboID_15_wholebrain_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_15_wholebrain',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace5 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_72_LS1_log2FC'],
 y=merge_df_plotly['TDP43TurboID_72_LS1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_72_LS1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace6 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_72_wholebrain_log2FC'],
 y=merge_df_plotly['TDP43TurboID_72_wholebrain_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_72_wholebrain',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace7 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_saline_LP1_log2FC'],
 y=merge_df_plotly['TDP43TurboID_saline_LP1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_saline_LP1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace8 = go.Scatter(
 x=merge_df_plotly['TDP43TurboID_saline_LS1_log2FC'],
 y=merge_df_plotly['TDP43TurboID_saline_LS1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TDP43TurboID_saline_LS1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace9 = go.Scatter(
 x=merge_df_plotly['TurboID_15_wholebrain_log2FC'],
 y=merge_df_plotly['TurboID_15_wholebrain_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TurboID_15_wholebrain',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace10 = go.Scatter(
 x=merge_df_plotly['TurboID_72_LP1_log2FC'],
 y=merge_df_plotly['TurboID_72_LP1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TurboID_72_LP1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace11 = go.Scatter(
 x=merge_df_plotly['TurboID_72_LS1_log2FC'],
 y=merge_df_plotly['TurboID_72_LS1_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TurboID_72_LS1',
 hovertext=list(merge_df_plotly.Protein_Name)
)

trace12 = go.Scatter(
 x=merge_df_plotly['TurboID_72_wholebrain_log2FC'],
 y=merge_df_plotly['TurboID_72_wholebrain_neg_log_pval'],
 mode='markers',
 marker = {"opacity": opacity, "size" : size},
 name='TurboID_72_wholebrain',
 hovertext=list(merge_df_plotly.Protein_Name)
)

In [14]:
fig = go.Figure()
fig.add_trace(trace12)
fig.add_trace(trace1)
fig.add_trace(trace2)
fig.add_trace(trace3)
fig.add_trace(trace4)
fig.add_trace(trace5)
fig.add_trace(trace6)
fig.add_trace(trace7)
fig.add_trace(trace8)
fig.add_trace(trace9)
fig.add_trace(trace10)
fig.add_trace(trace11)
fig.update_layout(title='Volcano plot', width=1500, height=1000)
fig.show()